In [69]:
import ast

import numpy as np
import pandas as pd
from sqlalchemy import create_engine

pd.set_option('display.max_rows', None)

engine = create_engine('sqlite:///data/books.db')

In [70]:
def read_db(table_name: str):
    sql = f'SELECT * FROM {table_name}'
    return pd.read_sql(sql, engine)

oclc = read_db('books_oclc')
kag = read_db('books_kaggle')
cat = read_db('categories')

for db in [oclc, kag, cat]:
    db = db.replace('', np.nan)

In [71]:
kag['publication_year'] = kag.publication_date.str.extract('(?<=/)(\d{4})')

In [72]:
oclc.loc[
    oclc.publication_year.str.contains('\D'),
    'publication_year'
] = np.nan

In [73]:
oclc.head()

owi         isbn13  \
0  5453582619                  
1  3770153674                  
2  3810426007  9780439554893   
3  3770153674                  
4              9780439682589   

                                               title  \
0                                                      
1                                                      
2            Harry Potter And The Chamber Of Secrets   
3                                                      
4  Harry Potter - 5 Years Of Magic, Adventure, An...   

                              authors        publisher publication_year  \
0                                                                         
1                                                                         
2  ['J. K. Rowling', 'Mary GrandPre']  Arthur a Levine             2003   
3                                                                         
4                   ['J. K. Rowling']       Scholastic             2004   

  language_code      oclc         lcc   ddf  \
0                                      None   
1                                      None   
2            en  40043650  PR6068.O93  None   
3                                      None   
4            en                        None   

                                          categories      ddc  
0                                                              
1                                                              
2  {'1219920': 'England', '1729962': 'Hogwarts Sc...  823.914  
3                                                              
4

In [74]:
ser_list = []
def get_titles_cats(cat_code: str):
    titles_ser = oclc.loc[oclc['categories'].str.contains(cat_code), 'title']
    titles_ser.index = np.repeat(cat_code, len(titles_ser))
    ser_list.append(titles_ser)

cat.cat_code.apply(get_titles_cats)

0       None
1       None
2       None
3       None
4       None
5       None
6       None
7       None
8       None
9       None
10      None
11      None
12      None
13      None
14      None
15      None
16      None
17      None
18      None
19      None
20      None
21      None
22      None
23      None
24      None
25      None
26      None
27      None
28      None
29      None
30      None
31      None
32      None
33      None
34      None
35      None
36      None
37      None
38      None
39      None
40      None
41      None
42      None
43      None
44      None
45      None
46      None
47      None
48      None
49      None
50      None
51      None
52      None
53      None
54      None
55      None
56      None
57      None
58      None
59      None
60      None
61      None
62      None
63      None
64      None
65      None
66      None
67      None
68      None
69      None
70      None
71      None
72      None
73      None
74      None
75      None
76      None

In [75]:
books_cats = pd.concat(ser_list).reset_index(drop=False).drop_duplicates()
books_cats.columns = ['cat_code', 'title']

In [76]:
from sqlalchemy import Text

books_cats.to_sql('titles__cat_codes',
                  engine,
                  index=False,
                  if_exists='replace', # May want to change this
                  dtype={
                      'cat_code': Text,
                      'title': Text,
                  })

## Replace Kaggle authors with OCLC authors

In [77]:
authors_list = []

def get_authors(multi_authors_entry):
    if multi_authors_entry:
        authors_list.append(ast.literal_eval(multi_authors_entry))

oclc.authors.apply(get_authors)


0        None
1        None
2        None
3        None
4        None
5        None
6        None
7        None
8        None
9        None
10       None
11       None
12       None
13       None
14       None
15       None
16       None
17       None
18       None
19       None
20       None
21       None
22       None
23       None
24       None
25       None
26       None
27       None
28       None
29       None
30       None
31       None
32       None
33       None
34       None
35       None
36       None
37       None
38       None
39       None
40       None
41       None
42       None
43       None
44       None
45       None
46       None
47       None
48       None
49       None
50       None
51       None
52       None
53       None
54       None
55       None
56       None
57       None
58       None
59       None
60       None
61       None
62       None
63       None
64       None
65       None
66       None
67       None
68       None
69       None
70       None
71    

In [78]:
from itertools import chain
authors_list_flat = list(chain(*authors_list))
authors_ser = pd.Series(authors_list_flat).drop_duplicates()

In [79]:
titles_by_author_list = []
def get_author_titles(author):
    try:
        titles_by_author = oclc.loc[oclc.authors.str.contains(author), 'title']
        titles_by_author.index = np.repeat(author, len(titles_by_author))
        titles_by_author_list.append(titles_by_author)
    except:
        print(author)

authors_ser.apply(get_author_titles)

C:\Users\THELET~1\AppData\Local\Temp/ipykernel_12048/3028403516.py:4: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  titles_by_author = oclc.loc[oclc.authors.str.contains(author), 'title']


Augustin ((saint ;)
Zi Sun (philosophe).)
Apollodore d'Athènes ((auteur prétendu ;)


0        None
1        None
3        None
5        None
9        None
18       None
20       None
22       None
23       None
24       None
25       None
26       None
27       None
28       None
29       None
30       None
31       None
32       None
33       None
34       None
35       None
36       None
37       None
38       None
40       None
41       None
42       None
49       None
51       None
52       None
53       None
54       None
56       None
57       None
58       None
62       None
63       None
64       None
65       None
66       None
68       None
70       None
74       None
76       None
77       None
79       None
80       None
81       None
82       None
83       None
84       None
85       None
87       None
90       None
91       None
92       None
94       None
95       None
97       None
98       None
100      None
101      None
103      None
104      None
105      None
106      None
107      None
108      None
109      None
110      None
111      None
112   

In [83]:
# (pd.concat(titles_by_author_list).index != '').sum()
# oclc.loc[oclc.authors == ''].shape
# oclc.dropna(axis=0, how='any', subset=['authors', 'title']).shape
# oclc.replace('', np.nan).dropna(axis=0, how='any', subset=['authors', 'title']).shape
# oclc.shape
pd.concat(titles_by_author_list)

J. K. Rowling                                                                                                                                  Harry Potter And The Chamber Of Secrets
J. K. Rowling                                                                                                                        Harry Potter - 5 Years Of Magic, Adventure, An...
J. K. Rowling                                                                                                                                 Harry Potter And The Prisoner Of Azkaban
J. K. Rowling                                                                                                                                  Fantastic Beasts And Where To Find Them
J. K. Rowling                                                                                                                                   Harry Potter And The Half-Blood Prince
J. K. Rowling                                                                        